In [ ]:
# -*- coding: utf-8 -*-
import re
from pathlib import Path
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.ticker import FormatStrFormatter
from google.colab import files

# === Config: axis thickness + figure label ===
AXIS_LINE        = 5
FIG_LABEL_TEXT   = "(b)"
FIG_LABEL_COLOR  = "#000080"
FIG_LABEL_SIZE   = 60

# Ticks/limits
X_TICKS = [0, 2, 4, 6, 8]
Y_TICKS = [0, 400, 800, 1200, 1600]
X_LIMS  = (0, 8.10)   # small cushion past 8 so curves don't touch the "8" tick
Y_LIMS  = (0, 1600)

# === 1) Upload & resolve actual saved filename ===
print("📁 UPLOAD AS.xlsx NOW:")
uploaded = files.upload()
if not uploaded:
    raise RuntimeError("No file uploaded.")
xlsx_candidates = sorted(Path('.').glob('*.xlsx'),
                         key=lambda p: p.stat().st_mtime, reverse=True)
filename = str(xlsx_candidates[0])
print(f"📦 Using file on disk: {filename}")

# === 2) Required sheets ===
sheets = ['Test_1', 'Test_2', 'Test_3'] # Corrected 'Tes_3' to 'Test_3'

# === 3) Column finders (MPa only) ===
def find_strain_and_stress_mpa_cols(df):
    """Return (strain_col, stress_mpa_col).
       Requires a Stress column explicitly in MPa (header contains both 'stress' and 'mpa')."""
    cols = [c for c in df.columns if isinstance(c, str)]
    low  = [c.lower() for c in cols]

    # Strain: prefer headers with %; else any containing 'strain'
    cand_idx = [i for i, s in enumerate(low) if 'strain' in s]
    if not cand_idx:
        raise ValueError(f"Could not find a strain column. Columns: {cols}")
    strain_idx = next((i for i in cand_idx if ('%' in low[i]) or ('percent' in low[i])), cand_idx[0])
    strain_col = cols[strain_idx]

    # Stress in MPa: header must contain 'stress' and 'mpa'
    stress_idx = None
    for i, s in enumerate(low):
        if 'stress' in s and 'mpa' in s:
            stress_idx = i
            break
    if stress_idx is None:
        raise ValueError(
            "Could not find a Stress (MPa) column. "
            "Please ensure the header includes both 'Stress' and 'MPa'. "
            f"Columns seen: {cols}"
        )
    stress_col = cols[stress_idx]
    return strain_col, stress_col

# === 4) Read workbook & build tidy dataframe (NO conversion; uses MPa as-is) ===
xls = pd.ExcelFile(filename)
print(f"📑 Sheets found in workbook: {xls.sheet_names}")
missing = [s for s in sheets if s not in xls.sheet_names]
if missing:
    raise RuntimeError(f"The workbook must contain all four sheets {sheets}, "
                       f"but these are missing: {missing}")

df_list = []
for sheet in sheets:
    df_raw = pd.read_excel(xls, sheet_name=sheet)
    print(f"\n🔍 COLUMNS IN {sheet}: {list(df_raw.columns)}")
    strain_col, stress_col = find_strain_and_stress_mpa_cols(df_raw)
    print(f"✅ Using Strain: '{strain_col}' | Stress (MPa): '{stress_col}' for {sheet}")

    s = pd.to_numeric(df_raw[strain_col], errors='coerce')
    # If strain is fractional (0–1), convert to percent; else assume already in %
    s_percent = 100.0 * s if s.max(skipna=True) is not None and s.max(skipna=True) <= 1.1 else s
    stress_mpa = pd.to_numeric(df_raw[stress_col], errors='coerce')

    dfi = (pd.DataFrame({'Strain(%)': s_percent, 'Stress (MPa)': stress_mpa, 'Sheet': sheet})
             .dropna(subset=['Strain(%)', 'Stress (MPa)'])
             .sort_values('Strain(%)')
             .drop_duplicates(subset=['Strain(%)'], keep='last'))
    df_list.append(dfi)

df = pd.concat(df_list, ignore_index=True)
print(f"\n✅ LOADED: {filename} (all 4 sheets)")
print(f"📊 TOTAL ROWS: {len(df)} — columns: {list(df.columns)}")

# === 5) Styling ===
plt.rcParams.update({
    'font.family': 'serif',
    'font.size': 12,
    'axes.linewidth': AXIS_LINE,
    'mathtext.default': 'regular',
    'lines.linewidth': 7,
    'lines.solid_capstyle': 'round'
})
plt.rcParams['font.serif'] = ["Palatino Linotype", "Palatino", "URW Palladio L"] + plt.rcParams.get('font.serif', [])

# === 6) Plot ===
plt.figure(figsize=(10.5, 7.8), dpi=1200)
colors = ['#D55E00', '#E69F00', '#56B4E9', '#009E73']  # distinct/colorblind-friendly

for i, sheet in enumerate(sheets):
    d = df[df['Sheet'] == sheet]
    plt.plot(d['Strain(%)'], d['Stress (MPa)']
             ,label=f'AS_Test {i+1}', color=colors[i], zorder=2)

# Axis labels (bold)
plt.xlabel(r'$\epsilon$ (%)', fontsize=40, fontweight='bold')
plt.ylabel(r'$\sigma$ (MPa)', fontsize=40, fontweight='bold')

ax = plt.gca()
# Spines
for side in ('left', 'bottom', 'right', 'top'):
    ax.spines[side].set_linewidth(AXIS_LINE)
ax.spines['top'].set_visible(False)
ax.spines['right'].set_visible(False)

# Fixed ticks & limits (with tiny right cushion)
ax.set_xticks(X_TICKS)
ax.set_yticks(Y_TICKS)
ax.set_xlim(*X_LIMS)
ax.set_ylim(*Y_LIMS)
ax.yaxis.set_major_formatter(FormatStrFormatter('%d'))

# Thick, bold ticks
ax.tick_params(axis='both', which='major',
               labelsize=38, width=AXIS_LINE, length=10, direction='out', pad=8)
for t in ax.get_xticklabels() + ax.get_yticklabels():
    t.set_fontweight('bold')

# Figure label at top-center
ax.text(0.5, 1.02, FIG_LABEL_TEXT,
        transform=ax.transAxes,
        ha='center', va='bottom',
        fontsize=FIG_LABEL_SIZE, color=FIG_LABEL_COLOR, fontweight='bold')

# Legend (bold, ordered 1→4)
handles, labels = ax.get_legend_handles_labels()
desired = [f'AS_Test {i}' for i in range(1, 5)]
order = [labels.index(x) for x in desired if x in labels]
leg = ax.legend([handles[i] for i in order], [labels[i] for i in order],
                loc='lower right', bbox_to_anchor=(0.95, 0.02),
                fontsize=30, framealpha=0.85, borderpad=0.6, labelspacing=0.6, fancybox=True)
for txt in leg.get_texts():
    txt.set_fontweight('bold')

plt.tight_layout()
plt.subplots_adjust(left=0.14, bottom=0.12)

# === 7) Save THEN show ===
outname = 'LPBF_SDSS2507_AS_Stress_Strain.png'
plt.savefig(outname, format='png', dpi=1200, bbox_inches='tight')
plt.show()

print("🎉 ULTRA-HIGH-DPI PNG SAVED!")
print(f"📄 Filename: {outname}")
print(f"🔧 Axis & tick thickness set via AXIS_LINE = {AXIS_LINE}")
print(f"🏷️ Figure label: {FIG_LABEL_TEXT} (size {FIG_LABEL_SIZE}, color {FIG_LABEL_COLOR})")

📁 UPLOAD AS.xlsx NOW:


Saving AS.xlsx to AS (5).xlsx
📦 Using file on disk: AS (5).xlsx
📑 Sheets found in workbook: ['Test_1', 'Test_2', 'Test_3']

🔍 COLUMNS IN Test_1: ['Strain(%)', 'Stress(MPa)']
✅ Using Strain: 'Strain(%)' | Stress (MPa): 'Stress(MPa)' for Test_1

🔍 COLUMNS IN Test_2: ['Strain(%)', 'Stress (MPa)']
✅ Using Strain: 'Strain(%)' | Stress (MPa): 'Stress (MPa)' for Test_2

🔍 COLUMNS IN Test_3: ['Strain(%)', 'Stress(MPa)']
✅ Using Strain: 'Strain(%)' | Stress (MPa): 'Stress(MPa)' for Test_3

✅ LOADED: AS (5).xlsx (all 4 sheets)
📊 TOTAL ROWS: 1296 — columns: ['Strain(%)', 'Stress (MPa)', 'Sheet']


🎉 ULTRA-HIGH-DPI PNG SAVED!
📄 Filename: LPBF_SDSS2507_AS_Stress_Strain.png
🔧 Axis & tick thickness set via AXIS_LINE = 5
🏷️ Figure label: (b) (size 60, color #000080)


In [ ]:
# -*- coding: utf-8 -*-
import re
from pathlib import Path
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.ticker import FormatStrFormatter
from google.colab import files

# === SERIES & styling ===
SERIES = "SR300_5h"

AXIS_LINE        = 5
FIG_LABEL_TEXT   = "(c)"
FIG_LABEL_COLOR  = "#000080"
FIG_LABEL_SIZE   = 60

# Ticks/limits (tiny cushion past 8 so curves don't touch the "8" tick)
X_TICKS = [0, 2, 4, 6, 8]
Y_TICKS = [0, 400, 800, 1200, 1600]
X_LIMS  = (0, 8.10)
Y_LIMS  = (0, 1600)

# === 1) Upload & resolve actual saved filename ===
print(f"📁 UPLOAD {SERIES}.xlsx NOW:")
uploaded = files.upload()
if not uploaded:
    raise RuntimeError("No file uploaded.")
xlsx_candidates = sorted(Path('.').glob('*.xlsx'),
                         key=lambda p: p.stat().st_mtime, reverse=True)
filename = str(xlsx_candidates[0])
print(f"📦 Using file on disk: {filename}")

# === 2) Required sheets (exact spellings) ===
sheets = ['Test_1', 'Test_2', 'Test_3']

# === 3) Column finders (expects Stress explicitly in MPa) ===
def find_strain_and_stress_mpa_cols(df):
    cols = [c for c in df.columns if isinstance(c, str)]
    low  = [c.lower() for c in cols]

    cand_idx = [i for i, s in enumerate(low) if 'strain' in s]
    if not cand_idx:
        raise ValueError(f"Could not find a strain column. Columns: {cols}")
    strain_idx = next((i for i in cand_idx if ('%' in low[i]) or ('percent' in low[i])), cand_idx[0])
    strain_col = cols[strain_idx]

    stress_idx = None
    for i, s in enumerate(low):
        if 'stress' in s and 'mpa' in s:
            stress_idx = i
            break
    if stress_idx is None:
        raise ValueError("Could not find a Stress (MPa) column. Columns: {cols}")
    stress_col = cols[stress_idx]
    return strain_col, stress_col

# === 4) Read workbook & build tidy dataframe (use MPa as-is) ===
xls = pd.ExcelFile(filename)
missing = [s for s in sheets if s not in xls.sheet_names]
if missing:
    raise RuntimeError(f"Workbook must contain these sheets {sheets}, but missing: {missing}")

df_list = []
for sheet in sheets:
    df_raw = pd.read_excel(xls, sheet_name=sheet)
    strain_col, stress_col = find_strain_and_stress_mpa_cols(df_raw)

    s = pd.to_numeric(df_raw[strain_col], errors='coerce')
    s_percent = 100.0 * s if s.max(skipna=True) is not None and s.max(skipna=True) <= 1.1 else s
    stress_mpa = pd.to_numeric(df_raw[stress_col], errors='coerce')

    dfi = (pd.DataFrame({'Strain(%)': s_percent, 'Stress (MPa)': stress_mpa, 'Sheet': sheet})
             .dropna(subset=['Strain(%)', 'Stress (MPa)'])
             .sort_values('Strain(%)')
             .drop_duplicates(subset=['Strain(%)'], keep='last'))
    df_list.append(dfi)

df = pd.concat(df_list, ignore_index=True)

# === 5) Styling ===
plt.rcParams.update({
    'font.family': 'serif',
    'font.size': 12,
    'axes.linewidth': AXIS_LINE,
    'mathtext.default': 'regular',
    'lines.linewidth': 7,
    'lines.solid_capstyle': 'round'
})
plt.rcParams['font.serif'] = ["Palatino Linotype", "Palatino", "URW Palladio L"] + plt.rcParams.get('font.serif', [])

# === 6) Plot ===
plt.figure(figsize=(10.5, 7.8), dpi=1200)

# DISTINCT palette (not AS)
colors = ['#3B528B', '#21908C', '#5DC863', '#440154']

for i, sheet in enumerate(sheets, start=1):
    d = df[df['Sheet'] == sheet]
    # ⬇️ Two-line legend label: series on first line, test on second line
    two_line_label = f"{SERIES}\n_Test {i}"
    plt.plot(d['Strain(%)'], d['Stress (MPa)'],
             label=two_line_label, color=colors[i-1], zorder=2)

# Axis labels (bold)
plt.xlabel(r'$\epsilon$ (%)', fontsize=40, fontweight='bold')
plt.ylabel(r'$\sigma$ (MPa)', fontsize=40, fontweight='bold')

ax = plt.gca()
for side in ('left', 'bottom', 'right', 'top'):
    ax.spines[side].set_linewidth(AXIS_LINE)
ax.spines['top'].set_visible(False)
ax.spines['right'].set_visible(False)

ax.set_xticks(X_TICKS); ax.set_yticks(Y_TICKS)
ax.set_xlim(*X_LIMS);   ax.set_ylim(*Y_LIMS)
ax.yaxis.set_major_formatter(FormatStrFormatter('%d'))

ax.tick_params(axis='both', which='major',
               labelsize=38, width=AXIS_LINE, length=10, direction='out', pad=8)
for t in ax.get_xticklabels() + ax.get_yticklabels():
    t.set_fontweight('bold')

# Figure label below x-axis (as your example)
ax.text(0.5, -0.25, FIG_LABEL_TEXT,
        transform=ax.transAxes,
        ha='center', va='top',
        fontsize=FIG_LABEL_SIZE, color=FIG_LABEL_COLOR, fontweight='bold')

# Legend: keep order Test 1→4; labels are already two-line strings
leg = ax.legend(loc='lower right', bbox_to_anchor=(1, 0.02),
                fontsize=26, framealpha=0.85, borderpad=0.6,
                labelspacing=0.6, handlelength=0.5, fancybox=True)
for txt in leg.get_texts():
    txt.set_fontweight('bold')

plt.tight_layout()
plt.subplots_adjust(left=0.14, bottom=0.22)  # extra bottom for label

# === 7) Save THEN show ===
outname = f'{SERIES}_Stress_Strain.png'
plt.savefig(outname, format='png', dpi=1200, bbox_inches='tight')
plt.show()

print("🎉 ULTRA-HIGH-DPI PNG SAVED!")
print(f"📄 Filename: {outname}")


📁 UPLOAD SR300_5h.xlsx NOW:


Saving SR300_5h.xlsx to SR300_5h (13).xlsx
📦 Using file on disk: SR300_5h (13).xlsx


🎉 ULTRA-HIGH-DPI PNG SAVED!
📄 Filename: SR300_5h_Stress_Strain.png


In [ ]:
# -*- coding: utf-8 -*-
import re
from pathlib import Path
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.ticker import FormatStrFormatter
from google.colab import files

# === SERIES & styling ===
SERIES = "SA1100_15min"

AXIS_LINE        = 5
FIG_LABEL_TEXT   = "(d)"
FIG_LABEL_COLOR  = "#000080"
FIG_LABEL_SIZE   = 60

# Ticks/limits
X_TICKS = [0, 2, 4, 6, 8]
Y_TICKS = [0, 400, 800, 1200, 1600]
X_LIMS  = (0, 8.10)
Y_LIMS  = (0, 1600)

# === 1) Upload & resolve actual saved filename ===
print(f"📁 UPLOAD {SERIES}.xlsx NOW:")
uploaded = files.upload()
if not uploaded:
    raise RuntimeError("No file uploaded.")
xlsx_candidates = sorted(Path('.').glob('*.xlsx'),
                         key=lambda p: p.stat().st_mtime, reverse=True)
filename = str(xlsx_candidates[0])
print(f"📦 Using file on disk: {filename}")

# === 2) Required sheets ===
sheets = ['Test_1', 'Test_2', 'Test_3']

# === 3) Column finders (expects Stress explicitly in MPa) ===
def find_strain_and_stress_mpa_cols(df):
    cols = [c for c in df.columns if isinstance(c, str)]
    low  = [c.lower() for c in cols]

    cand_idx = [i for i, s in enumerate(low) if 'strain' in s]
    if not cand_idx:
        raise ValueError(f"Could not find a strain column. Columns: {cols}")
    strain_idx = next((i for i in cand_idx if ('%' in low[i]) or ('percent' in low[i])), cand_idx[0])
    strain_col = cols[strain_idx]

    stress_idx = None
    for i, s in enumerate(low):
        if 'stress' in s and 'mpa' in s:
            stress_idx = i
            break
    if stress_idx is None:
        raise ValueError("Could not find a Stress (MPa) column. Columns: {cols}")
    stress_col = cols[stress_idx]
    return strain_col, stress_col

# === 4) Read workbook & build tidy dataframe (use MPa as-is) ===
xls = pd.ExcelFile(filename)
missing = [s for s in sheets if s not in xls.sheet_names]
if missing:
    raise RuntimeError(f"Workbook must contain these sheets {sheets}, but missing: {missing}")

df_list = []
for sheet in sheets:
    df_raw = pd.read_excel(xls, sheet_name=sheet)
    strain_col, stress_col = find_strain_and_stress_mpa_cols(df_raw)

    s = pd.to_numeric(df_raw[strain_col], errors='coerce')
    s_percent = 100.0 * s if s.max(skipna=True) is not None and s.max(skipna=True) <= 1.1 else s
    stress_mpa = pd.to_numeric(df_raw[stress_col], errors='coerce')

    dfi = (pd.DataFrame({'Strain(%)': s_percent, 'Stress (MPa)': stress_mpa, 'Sheet': sheet})
             .dropna(subset=['Strain(%)', 'Stress (MPa)'])
             .sort_values('Strain(%)')
             .drop_duplicates(subset=['Strain(%)'], keep='last'))
    df_list.append(dfi)

df = pd.concat(df_list, ignore_index=True)

# === 5) Styling ===
plt.rcParams.update({
    'font.family': 'serif',
    'font.size': 12,
    'axes.linewidth': AXIS_LINE,
    'mathtext.default': 'regular',
    'lines.linewidth': 7,
    'lines.solid_capstyle': 'round'
})
plt.rcParams['font.serif'] = ["Palatino Linotype", "Palatino", "URW Palladio L"] + plt.rcParams.get('font.serif', [])

# === 6) Plot ===
plt.figure(figsize=(10.5, 7.8), dpi=1200)

# NEW distinct palette (Tol Vibrant) — different from SR300_5h
colors = ['#EE6677',  # coral
          '#228833',  # purple
          '#4477AA',  # blue
]
for i, sheet in enumerate(sheets, start=1):
    d = df[df['Sheet'] == sheet]
    two_line_label = f"{SERIES}\n_Test {i}"
    plt.plot(d['Strain(%)'], d['Stress (MPa)'],
             label=two_line_label, color=colors[i-1], zorder=2)

# Axis labels (bold)
plt.xlabel(r'$\epsilon$ (%)', fontsize=40, fontweight='bold')
plt.ylabel(r'$\sigma$ (MPa)', fontsize=40, fontweight='bold')

ax = plt.gca()
for side in ('left', 'bottom', 'right', 'top'):
    ax.spines[side].set_linewidth(AXIS_LINE)
ax.spines['top'].set_visible(False)
ax.spines['right'].set_visible(False)

ax.set_xticks(X_TICKS); ax.set_yticks(Y_TICKS)
ax.set_xlim(*X_LIMS);   ax.set_ylim(*Y_LIMS)
ax.yaxis.set_major_formatter(FormatStrFormatter('%d'))

ax.tick_params(axis='both', which='major',
               labelsize=38, width=AXIS_LINE, length=10, direction='out', pad=8)
for t in ax.get_xticklabels() + ax.get_yticklabels():
    t.set_fontweight('bold')

# Figure label below x-axis
ax.text(0.5, -0.25, FIG_LABEL_TEXT,
        transform=ax.transAxes,
        ha='center', va='top',
        fontsize=FIG_LABEL_SIZE, color=FIG_LABEL_COLOR, fontweight='bold')

# Legend (two-line labels, bold)
leg = ax.legend(loc='lower right', bbox_to_anchor=(0.5, 0.5),
                fontsize=26, framealpha=0.85, borderpad=0.2,
                labelspacing=0.6, handlelength=0.3, fancybox=True)
for txt in leg.get_texts():
    txt.set_fontweight('bold')

plt.tight_layout()
plt.subplots_adjust(left=0.14, bottom=0.22)

# === 7) Save THEN show ===
outname = f'{SERIES}_Stress_Strain.png'
plt.savefig(outname, format='png', dpi=1200, bbox_inches='tight')
plt.show()

print("🎉 ULTRA-HIGH-DPI PNG SAVED!")
print(f"📄 Filename: {outname}")


📁 UPLOAD SA1100_15min.xlsx NOW:


Saving SA1100_15min.xlsx to SA1100_15min (9).xlsx
📦 Using file on disk: SA1100_15min (9).xlsx


🎉 ULTRA-HIGH-DPI PNG SAVED!
📄 Filename: SA1100_15min_Stress_Strain.png
